# 爬取定投课堂资料
通过解析课程json文件，获取对应资源的url从而下载所有资料
获取课程id

In [18]:
import json
import time

import requests
from IPython.display import Audio,display
from pydub import AudioSegment
import os
import random
import sqlite3

# with open('audio.json', encoding="UTF-8") as f:
#     json_data = json.load(f)
# print(type(json_data[1]))  # Output: dict
# TODO: 优化代码

# get audio form database
id = 491
conn = sqlite3.connect('course_database.db')
cursor = conn.cursor()
audio_data = cursor.execute('select JSON from JSON_DATA jd where id = ?', (id,)).fetchall()
# json_data = cursor.fetchall()[0][0]
json_string = audio_data[0][0] if audio_data else None
cursor.close()
conn.close()
json_data = json.loads(json_string)

# course_id =  str(json_data[1]['course_id'])
course_title = json_data["data"]["title"].replace(".", "_").replace("/", "_")
os.makedirs(course_title, exist_ok=True)

# 遍历
audio_list = []
for audio in json_data['data']['course_contents']:
    # t = random.randint(1, 10)
    # time.sleep(1)
    category = audio['category']
    # requests.adapters.DEFAULT_RETRIES = 100
    # 获取音频内容
    i = 1
    while i >= 1:
        try:
            if category == "audio":
                url = audio['attachment']['url']
                audio = requests.get(url)
                audio_list.append(audio.content)
            # 获取文本笔记
            elif category == "text":
                text = audio['content']
                print(text)
                with open(os.path.join(course_title, course_title + 'note.txt'), 'a') as file:
                        file.write(text)
                        file.write("\n")
            # 获取其他可下载附件
            elif category != "MESSAGE_RECALL":
                # print(audio['category'])
                if 'attachment' in audio:
                    url = audio['attachment']['url']
                    attachment = requests.get(url)
                    filename = os.path.basename(url)
                    with open(os.path.join(course_title, filename), 'wb') as file:
                        file.write(attachment.content)
            # 获取其他内容
            else:
                print(audio['category'])
                if 'attachment' in audio:
                    print(audio['attachment']['url'])
                print(audio['text'])
            i = 0
        except:
            i += 1
            print("get file failed")
            if 'attachment' in audio:
                    print(audio['attachment']['url'])

# 处理获取所有音频文件
audio_seg_list = []
try:
    for i in audio_list:
        with open('temp.mp3', 'wb') as file:
            file.write(i)  # 确保i是二进制数据
        audio_part = AudioSegment.from_mp3('temp.mp3')
        audio_seg_list.append(audio_part)
        
    x = sum(audio_seg_list)
    audio_name = course_title + '/' + course_title + '.mp3'
    x.export(audio_name, format="mp3")
    display(Audio(audio_name))
except Exception as e:
    print("合并音频时发生错误:", e)

例行公事
daily routine
睡觉 吃/排


## 获取图片url

In [4]:
# get all url and text
import json
import requests
from IPython.display import Audio,display
from pydub import AudioSegment
import os

# get pic url list


with open('audio.json', encoding= "UTF-8") as f:
    json_data = json.load(f)
# print(type(json_data[1]))  # Output: dict

course_title =  str(json_data[1]['course_title'])
# os.makedirs(course_title, exist_ok=True)

audio_list = []
for audio in json_data:
    category = audio['category']
    if category == "PLAIN_IMAGE":
            url = audio['attachment']['url']
            print(url)
            # with open( course_title + '_pic_url.txt', 'a') as file:
            #         file.write(url)
            #         file.write("\n")

https://xuexi-courses-storage.firesbox.com/7000102069/replay/78b6da46-ecd8-46fb-a857-423ca6da8196.png
